In [1]:
import pandas as pd # package for high-performance, easy-to-use data structures and data analysis // 数据处理库
import numpy as np # fundamental package for scientific computing with Python
from pyecharts.charts import Map
import matplotlib
from folium import plugins
import matplotlib.pyplot as plt # for plotting
import seaborn as sns # for making plots with seaborn
color = sns.color_palette()
from plotly.offline import init_notebook_mode, iplot,plot
init_notebook_mode(connected=True)
import plotly.graph_objs as go
import squarify
from numpy import array
from matplotlib import cm
import json
import folium
import requests
from fbprophet import Prophet

In [2]:
allurl='https://view.inews.qq.com/g2/getOnsInfo?name=disease_h5&callback=jQuery34109240263474975745_1581572984726&_=1581572984727'

In [3]:
response=requests.get(allurl)

In [4]:
response.encoding=response.apparent_encoding

In [5]:
m=response.text
js=json.loads(m[m.find('{'):-1])

In [6]:
jd=json.loads(js['data'])

In [7]:
with open(r'G:\chrome download\中国.json',encoding='utf-8') as f:
    china_geo=json.load(f)

In [8]:
code={'江西':'360000',
'河南':'410000',
'四川':'510000',
'重庆':'500000',
'西藏':'540000',
'贵州':'520000',
'辽宁':'210000',
'新疆':'650000',
'山东':'370000',
'上海':'310000',
'澳门':'820000',
'山西':'140000',
'浙江':'330000',
'海南':'460000',
'福建':'350000',
'青海':'630000',
'宁夏':'640000',
'湖北':'420000',
'甘肃':'620000',
'安徽':'340000',
'台湾':'710000',
'陕西':'610000',
'广西':'450000',
'天津':'120000',
'云南':'530000',
'黑龙江':'230000',
'广东':'440000',
'湖南':'430000',
'河北':'130000',
'内蒙古':'150000',
'吉林':'220000',
'江苏':'320000',
'北京':'110000',
'香港':'810000'}


In [17]:
area=[]
adcode=[]
s=[]
g=[]
q=[]
d=[]
tg=[]
ts=[]
td=[]
tq=[]
for each in jd['areaTree'][0]['children']:
    area.append(each['name'])
    g.append(int(each['total']['confirm']))
    s.append(int(each['total']['suspect']))
    d.append(int(each['total']['dead']))
    q.append(int(each['total']['heal']))
    tg.append(int(each['today']['confirm']))
    #ts.append(int(each['today']['suspect']))
    #td.append(int(each['today']['dead']))
    #tq.append(int(each['today']['heal']))
for each in area:
    adcode.append(int(code[each]))
data={'地区':area,
      '确诊':g,
      '疑似':s,
      '治愈':q,
      '死亡':d,
      '今日新增确诊':tg,
     # '今日新增疑似':ts,
     # '今日新增治愈':tq,
     # '今日新增死亡':td,
      'adcode':adcode}
total=jd['areaTree'][0]['total']
total_data=' 全国累计确认人数：'+str(total['confirm'])+'\n 全国累计疑似人数：'+str(total['suspect'])+'\n 全国累计治愈人数：'+str(total['heal'])+'\n 全国累计死亡人数：'+str(total['dead'])
datass=pd.DataFrame(data)
wuhan={'地区':area[0],'确诊':g[0],'治愈':q[0],'死亡':d[0], '疑似':s[0], '今日新增确诊':tg[0]
       #, '今日新增疑似':ts[0],'今日新增治愈':tq[0],'今日新增死亡':td[0],
      }
datas=datass.drop(index=0)


In [18]:
jw={}
for i in range(0,len(china_geo['features'])-1):
    k=china_geo['features'][i]['properties']['center']
    loc=[k[1],k[0]]
    jw[china_geo['features'][i]['properties']['adcode']]=loc

In [19]:
def setpoints(datas,wuhan,mpq,mpg,mpd):
    for i in range(1,len(datas)+1):
        datag=datas['地区'][i]+': \t'+'确诊：'+str(datas['确诊'][i])+'人\n'+'今日新增确诊：'+str(datas['今日新增确诊'][i])+'人'
        dataq=datas['地区'][i]+'\t'+"治愈："+str(datas['治愈'][i])+'人\n'#+'今日新增治愈：'+str(datas['今日新增治愈'][i])+'人'
        datad=datas['地区'][i]+'\t'+"死亡："+str(datas['死亡'][i])+'人\n'#+'今日新增死亡：'+str(datas['今日新增死亡'][i])+'人'
        folium.vector_layers.CircleMarker(
            location=jw[datas['adcode'][i]],
            radius=3,
            color='blue',
            fill_color='blue',
            fill_opacity=1 , 
            popup=folium.map.Popup(html=datag,max_width=20)).add_to(mpg)
        folium.vector_layers.CircleMarker(
            location=jw[datas['adcode'][i]],
            radius=3,
            color='blue',
            fill_color='blue',
            fill_opacity=1 , 
            popup=folium.map.Popup(html=dataq,max_width=20)).add_to(mpq)
        folium.vector_layers.CircleMarker(
            location=jw[datas['adcode'][i]],
            radius=3,
            color='blue',
            fill_color='blue',
            fill_opacity=1 , 
            popup=folium.map.Popup(html=datad,max_width=20)).add_to(mpd)
        
    whdatag=wuhan['地区']+':\n'+'确诊：'+str(wuhan['确诊'])+'人\n'+'今日新增确诊：'+str(wuhan['今日新增确诊'])+'人'
    whdataq=wuhan['地区']+':\n'+'治愈：'+str(wuhan['治愈'])+'人\n'#+'今日新增治愈：'+str(wuhan['今日新增治愈'])+'人'
    whdatad=wuhan['地区']+':\n'+"死亡："+str(wuhan['死亡'])+'人\n'#+'今日新增死亡：'+str(wuhan['今日新增死亡'])+'人'
    folium.vector_layers.CircleMarker(
    location=jw[420000],
    radius=3,
    color='blue',
    fill_color='blue',
    fill_opacity=1 , 
    popup=folium.map.Popup(html=whdatag,max_width=20)).add_to(mpg)
    folium.vector_layers.CircleMarker(
    location=jw[420000],
    radius=3,
    color='blue',
    fill_color='blue',
    fill_opacity=1 , 
    popup=folium.map.Popup(html=whdataq,max_width=20)).add_to(mpq)           
    folium.vector_layers.CircleMarker(
    location=jw[420000],
    radius=3,
    color='blue',
    fill_color='blue',
    fill_opacity=1 , 
    popup=folium.map.Popup(html=whdatad,max_width=20)).add_to(mpd)

In [20]:

map = folium.Map(
    location=[39.30029918615029, 103.88671875], # 初始化地图中心
    zoom_start=4,# 初始化放大级别
    # 设置地图样式，可选择其他瓦片(tile)
    tiles=('https://api.tiles.mapbox.com/v4/mapbox.streets/{z}/{x}/{y}.png'
           + '?access_token=pk.eyJ1IjoibHVrYXNtYXJ0aW5lbGxpIiwiYSI6ImNpem8'
           + '5dmhwazAyajIyd284dGxhN2VxYnYifQ.HQCmyhEXZUTz3S98FMrVAQ'),
    attr='China', # 显示在地图右下角的自定义文字
    min_zoom=3.2,
)
qc=folium.Choropleth(
    geo_data=china_geo, # 传入geojson
    data=datas, # 颜色数据
    columns=['adcode','治愈'],# 染色区域id，颜色相对深度列名
    key_on='feature.properties.adcode', # geojson区域id
    highlight=True,
    name="治愈",
    overlay=True,
    control=True,
    show=False,
    fill_color='BuGn',
    fill_opacity=0.7,
    line_opacity=0.2,
    #bins=[0,3,10,30,80,150,200,300,2000,5000]
    )
gc=folium.Choropleth(
    geo_data=china_geo, # 传入geojson
    name='确诊',
    data=datas, # 颜色数据
    overlay=True,
    highlight=True,
    control=True,
    columns=['adcode','确诊'],# 染色区域id，颜色相对深度列名
    key_on='feature.properties.adcode', # geojson区域id
    fill_color='YlOrRd',
    fill_opacity=0.7,
    line_opacity=0.2,
    #bins=[0, 10, 50, 100,200, 500,1000,5000,10000,50000]
    )
dc=folium.Choropleth(
    geo_data=china_geo, # 传入geojson
    name='死亡',
    data=datas, # 颜色数据
    overlay=True,
    highlight=True,
    control=True,
    columns=['adcode','死亡'],# 染色区域id，颜色相对深度列名
    key_on='feature.properties.adcode', # geojson区域id
    fill_color='OrRd',
    fill_opacity=0.7,
    line_opacity=0.2,
    show=False
    #bins=[0, 1, 2,4,7,11,16,22,25,1500]
    )
mpg=folium.map.FeatureGroup(name='g')
mpq=folium.map.FeatureGroup(name='q')
mpd=folium.map.FeatureGroup(name='d')
setpoints(datas,wuhan,mpq,mpg,mpd)
mpg.add_to(gc)
mpq.add_to(qc)
mpd.add_to(dc)
qc.add_to(map)
dc.add_to(map)
gc.add_to(map)
folium.map.Marker(location =[48.2871,138.4433],tooltip=total_data).add_to(map)
folium.map.LayerControl('bottomleft' ).add_to(map)
map.save('map.html')
map

In [21]:
token='pk.eyJ1IjoiMTc2Mjc2Njk2NjAiLCJhIjoiY2s2aTY4MTdjMGFiaTNrcWx0cGs5aWNjZCJ9.qRiapu6x8dHyZ9985q8j_Q'
china_geo2=china_geo
for each in china_geo2['features']:
    each['id']=each['properties']['adcode']
data={'地区':area,
      '确诊':g,
      '疑似':s,
      '治愈':q,
      '死亡':d,
      '今日新增确诊':tg,
     # '今日新增疑似':ts,
     # '今日新增治愈':tq,
     # '今日新增死亡':td,
      'adcode':adcode}
total=jd['areaTree'][0]['total']
total_data=' 全国累计确认人数：'+str(total['confirm'])+'\n 全国累计疑似人数：'+str(total['suspect'])+'\n 全国累计治愈人数：'+str(total['heal'])+'\n 全国累计死亡人数：'+str(total['dead'])
datass=pd.DataFrame(data)
wuhan={'地区':area[0],'确诊':g[0],'治愈':q[0],'死亡':d[0], '疑似':s[0], '今日新增确诊':tg[0]
       #, '今日新增疑似':ts[0],'今日新增治愈':tq[0],'今日新增死亡':td[0],
      }
datas=datass.drop(index=0)

In [28]:

trace1= go.Choroplethmapbox(
        name='确诊人数',
        geojson=china_geo2,
        ids=datas.adcode,
        locations=datass['adcode'],
        z=datas['确诊'],
        text=datass['地区'],
        hoverinfo= 'text+z+name',
        colorscale='YlOrRd',
        marker_line_width=0.5)
trace2=go.Choroplethmapbox(
        name='治愈人数',
        geojson=china_geo2,
        ids=datas.adcode,
        locations=datass['adcode'],
        z=datass['治愈'],
        text=datass['地区'],
        hoverinfo= 'text+z+name',
        colorscale='BuGn',
        marker_line_width=0.5)
trace3=go.Choroplethmapbox(
        name='死亡人数',
        geojson=china_geo2,
        ids=datas.adcode,
        locations=datass['adcode'],
        z=datass['死亡'],
        text=datass['地区'],
        hoverinfo= 'text+z+name',
        colorscale='OrRd',
        marker_line_width=0.5)
data1=[trace1]
data2=[trace2]
data3=[trace3]
layout=dict(mapbox={'accesstoken':token,
                          'center':{'lon':103,'lat':39},
                              'zoom':2.5},
                          title={'text':'result','xref':'paper','x':0.4},
            
                          margin={'l':10,'r':0,'t':50,'b':10}
                  
                         )
fig1 = go.Figure(data=data1, layout=layout)
fig2 = go.Figure(data=data2, layout=layout)
fig3 = go.Figure(data=data3, layout=layout)
fig1.show()
fig2.show()
fig3.show()
